# Lecture du fichier csv de départ et tri selon l'attribut recorded_at

In [1]:
import csv
import math
from datetime import datetime


def create_timestamp(date):
    dt = datetime(int(date[0:4]), int(date[5:7]), int(date[8:10]), 
                   int(date[11:13]), int(date[14:16]), int(date[17:19]))
    return dt


P = []

file = input("Entrez le nom le fichier csv (avec l'extension) -> ")
with open(file, newline='') as csvfile:
    reader = csv.DictReader(csvfile)
    
    for row in reader:
        point = {}
        point['recorded_at'] = row['recorded_at']
        point['latitude'] = row['latitude']
        point['longitude'] = row['longitude']
        point['stamp'] = create_timestamp(row['recorded_at'])
        P.append(point)
        
        
P = sorted(P, key=lambda point: point['stamp'])   # tri selon timestamp(recorded_at)


print('done')

Entrez le nom le fichier csv (avec l'extension) -> 356232051084258.csv
done


# Application de l'algorithme des stay points

In [7]:

# in minutes
def time_gap(current, new):
    
    td = abs(current - new)
    res = td.total_seconds()/60
    
    return res

# in meters
def distance(lat1, lat2, lon1, lon2):
    R = 6372800  # Earth radius in meters
    phi1 = math.radians(lat1)
    phi2 = math.radians(lat2)
    dphi = math.radians(lat2 - lat1)
    dlambda = math.radians(lon2 - lon1)
    a = math.sin(dphi / 2) ** 2 + math.cos(phi1) * math.cos(phi2) * math.sin(dlambda / 2) ** 2
    d = 2 * R * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    return d


def algorithm_stayPoint_detection(P, distThreh, timeThreh):

    i = 0
    pointNum = len(P)
    print('taille', pointNum)
    SP = []

    while i < pointNum-1:
        
        j = i + 1
        
        while j < pointNum:
            dist = distance(float(P[i]['latitude']), float(P[j]['latitude']),
                            float(P[i]['longitude']), float(P[j]['longitude']))

            if dist > distThreh:
                break
                
            j+=1
        
        j-=1
        
        deltaT = time_gap(P[i]['stamp'], P[j]['stamp'])
        if deltaT > timeThreh:
            S = {}
            S['arv'] = i
            S['lev'] = j
            SP.append(S)
            i=j
        else:
            i+=1

            
    return SP


S = algorithm_stayPoint_detection(P, 200, 30)
    
print('done')

taille 482157
done


# Séparation des différents trips

In [3]:
border = 0
trips = []

for stayP in S:
    
    if stayP['arv'] <= border:
        border = stayP['lev']
    else:
        S ={}
        S['arv'] = border
        S['lev'] = stayP['arv']
        trips.append(S)
        border = stayP['lev']
        

if border < len(P)-1:
    S ={}
    S['arv'] = border
    S['lev'] = len(P)-1
    trips.append(S)

print('done')

done


# Création d'un nouveau fichier csv avec colonne TRIP

In [4]:
with open('new.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['TRIP','recorded_at','latitude','longitude'])
    num_trip = 0
    
    for trip in trips:
        num_trip += 1
        
        for i in range(trip['arv'], trip['lev']+1):
            writer.writerow([num_trip, P[i]['recorded_at'], P[i]['latitude'], P[i]['longitude']])

    
print('done')

done


# Création d'un dictionnaire de trips à partir du fichier new.csv

In [5]:
index = 1
 
m = None
current_trip = None

trip = []       # liste de points pour un trip
dictionary = [] # liste de trips


with open('new.csv', newline='') as file:
    reader = csv.DictReader(file)
    
    for row in reader:
        
        if index == 1:
            index += 1
            current_trip = row['TRIP'] # initialisation du trip courant 
            
            
        if row['TRIP'] != current_trip:
            current_trip = row['TRIP']
            dictionary.append(trip)
            trip = []
            
        point = {}
        point['trip'] = row['TRIP']
        point['recorded_at'] = row['recorded_at']
        point['latitude'] = row['latitude']
        point['longitude'] = row['longitude']
        trip.append(point)
   

dictionary.append(trip) # ajout du dernier trip
print('done')
print('Trips numérotés de 1 à '+ str(len(dictionary)))

done
Trips numérotés de 1 à 29


# Affichage des trips sur une carte

In [6]:
import folium
from random import randint
    
# conversion tuple rvb en hexadecimal    
def rgb_to_hex(rgb):
    hex = '%02x%02x%02x' % rgb
    return '#'+hex

def random_color():
    rand = (randint(0,255), randint(0,255), randint(0,255))
    return rgb_to_hex(rand)


# configuration de la map 
def trip_map(index, dico):
    
    global map
    
    first = 1
    
    #chaque trips
    for i in index:
        
        couleur = random_color()
        indice = 0
        arrivee = len(dico[i])-1
        
        # chaque points dans un trip
        for point in dico[i]:
            
            if first == 1:
                first +=1
                map = folium.Map(location=[point['latitude'], point['longitude']])

            # départ
            if indice == 0:
                folium.Marker(
                    location=[point['latitude'], point['longitude']],
                    popup= "Depart (trip "+str(i+1)+")\n"+point['recorded_at']
                ).add_to(map)
                
            # arrivée    
            elif indice == arrivee:
                folium.Marker(
                    location=[point['latitude'], point['longitude']],
                    popup= "Arrivee (trip "+str(i+1)+")\n"+point['recorded_at']
                ).add_to(map)
                
            else : 
                folium.Circle(
                    radius=0.9,
                    location=[point['latitude'], point['longitude']],
                    color= couleur,
                    fill=False,
                ).add_to(map) 
            
            indice += 1
    
    
map = None

entree = int(input("Entrez un entier entre 1 à "+ str(len(dictionary))+ " -> "))
indexs = []

while entree != -1 :
    
    if (entree-1) not in indexs and entree > 0 and entree <= len(dictionary):
        indexs.append(entree-1)
        
    entree = int(input("entrez un nouvel entier ou entrez -1 pour arrêter -> " ))
    

trip_map(indexs, dictionary)
print('done')

map # affichage

Entrez un entier entre 1 à 29 -> 4
entrez un nouvel entier ou entrez -1 pour arrêter -> 21
entrez un nouvel entier ou entrez -1 pour arrêter -> -1
done
